# Capstone Project-Battle of the Neighborhoods:

## Using historical crime data and location data to reveal potential customers for a security firm moving into the city Buffalo New York State

## Table Of Contents

* [Introduction: Business Problem](#introduction)
* [Data](#Data)
* [Methodology](#Methodology)
* [Analysis](#Analysis)
* [Results and Discussion](#Results)
* [Conclusion](#Conclusion)


## Introduction: Business Problem <a name="introduction"></a>

This project is designed to help a friend who is a security expert with plans to relocate to the City of Buffalo from Canada, create a portfolio of potential clients in the city of Buffalo New York State. 

His startup services is made up of security products, services, professional consultations. One of his major challenge is navigating through a new city and scoping out new areas and client, would prove a daunting task.

After a few hours of discussing the problem with him and his team, the following were identified as key issues that needed to be resolved

* Are there any data of crime rates?
* Where were the most committed?
* And finally what kind of Businesses are located around the crime rate?

The answers to these questions would help him know the potential target areas and customers that the company shall like to do business with.

Moreso, it will help to reduce  the cost of products/service promotions in the local media.

And finally help selling different products and services to different customers based on the type of crimes that prevails in their areas.

As a data scientist, tool that would be used for this projects to draw out insights shall include, a complete datasets of crimes and list of neighborhoods and their locations in the city of Buffalo, geolacator,geopy, folium python libraries to draw, locates positions on the map of Buffalo and foursquare API to extract the venues from the coordinates that will be superimposed on the map

<a id='item1'></a>

## Data <a name="data"></a>

To reolve the three key issues raised by my friend, the data that will be used for this project will contain information vital for the projects. It must be a location datasets and luckily for us the city of Buffalo  has a repository of data in the website sites. 

The dataset for crime rates will be download via [OPEN DATA BUFFALO](https://data.buffalony.gov/Public-Safety/Crime-Incidents/d6g9-xbgu) and it contains yearly reports of crimes committed and reported, with corresponding crime locations in the city of Buffalo, New York state from 2009 to 2018 and last updated in 2018

The second dataset containing the list of neighborhoods with their corresponding coordinates was also downloaded via this link [OPEN DATA BUFFALO](https://data.buffalony.gov/browse?limitTo=maps)

We will be working with the 2018 reports for both the crimes rate and neighborhoods so the data would undergo some forms of cleaning


#### Libraries

All the libraries required for this project will be downloaded here in the first column

In [1]:
import numpy as np
import pandas as pd
import calendar
import json
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import geopy
from geopy.geocoders import Nominatim
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
import folium
from pandas.io.json import json_normalize
import geocoder
import requests
from folium import plugins
print('All libraries imported!')

All libraries imported!


<a id='item1'></a>

Reading the first dataset to a dataframe

In [2]:
#here pandas is used to read the csv fike into a dataframe
df1 = pd.read_csv('crime-incidents-1.csv', low_memory=False)
df1.head()

incident_id case_number       incident_datetime incident_type_primary  \
0    806461606  17-1410281  05/21/2017 07:53:00 AM               ASSAULT   
1    775993048  16-2830116  10/09/2016 03:17:25 AM         LARCENY/THEFT   
2    701886568  15-0550952  02/24/2015 09:59:00 AM               ASSAULT   
3    728282183  15-2350781  06/19/2015 08:00:00 AM              BURGLARY   
4    711185846  15-0860249  03/26/2015 06:00:00 AM         LARCENY/THEFT   

  incident_description  clearance_type            address_1  address_2  \
0              ASSAULT             NaN  1 Block FOUNTAIN PA        NaN   
1        LARCENY/THEFT             NaN    1 Block HERMAN ST        NaN   
2              ASSAULT             NaN    100 Block HAMBURG        NaN   
3             BURGLARY             NaN  200 Block EDISON AV        NaN   
4        LARCENY/THEFT             NaN  100 Block OXFORD AV        NaN   

      city state    zip country   latitude  longitude              created_at  \
0  BUFFALO    NY    NaN     NaN  42.977840 -78.824289  05/22/2017 06:04:48 AM   
1  BUFFALO    NY    NaN     NaN  42.893997 -78.844936  10/10/2016 04:06:33 AM   
2  BUFFALO    NY    NaN     NaN  42.868172 -78.858852  02/25/2015 07:06:19 AM   
3  BUFFALO    NY    NaN     NaN  42.931101 -78.802412  08/24/2015 06:07:27 AM   
4  BUFFALO    NY  14226     NaN  42.966698 -78.818852  03/28/2015 06:06:44 AM   

               updated_at                                    location  \
0  05/28/2017 06:07:24 AM  POINT (-78.8242894263842 42.9778397412646)   
1  10/16/2016 06:08:37 AM    POINT (-78.844935658937 42.893996842697)   
2  03/02/2015 07:12:21 AM    POINT (-78.858852415049 42.868171640149)   
3  08/30/2015 06:08:50 AM    POINT (-78.802412189146 42.931100982182)   
4  04/03/2015 06:07:10 AM              POINT (-78.8188515 42.9666981)   

   hour_of_day day_of_week parent_incident_type  Council Districts  \
0            7      Sunday              Assault                NaN   
1            3      Sunday                Theft                5.0   
2            9     Tuesday              Assault                5.0   
3            8      Friday  Breaking & Entering                8.0   
4            6    Thursday                Theft                NaN   

   Police Districts  Zip Codes  Tracts  
0               NaN       20.0     NaN  
1               3.0        8.0    26.0  
2               4.0       19.0    32.0  
3               2.0       11.0    63.0  
4               NaN        6.0     NaN

<a id='item1'></a>

## Data Cleaning

After exploring the dataset, some features that will not be needed will be dropped while the NaN values will be dropped as well

The date is in dd/mm/yyyy format and will be convert to dd-mm-yyyyn formaat

In [3]:
# converting the datetime format to dd-mm-yyyy
df1['created_at'] = pd.to_datetime(df1['created_at'])
df1['year'], df1['month'] = df1['created_at'].apply(lambda x: x.year), df1['created_at'].apply(lambda x: x.month)
df1.head()

incident_id case_number       incident_datetime incident_type_primary  \
0    806461606  17-1410281  05/21/2017 07:53:00 AM               ASSAULT   
1    775993048  16-2830116  10/09/2016 03:17:25 AM         LARCENY/THEFT   
2    701886568  15-0550952  02/24/2015 09:59:00 AM               ASSAULT   
3    728282183  15-2350781  06/19/2015 08:00:00 AM              BURGLARY   
4    711185846  15-0860249  03/26/2015 06:00:00 AM         LARCENY/THEFT   

  incident_description  clearance_type            address_1  address_2  \
0              ASSAULT             NaN  1 Block FOUNTAIN PA        NaN   
1        LARCENY/THEFT             NaN    1 Block HERMAN ST        NaN   
2              ASSAULT             NaN    100 Block HAMBURG        NaN   
3             BURGLARY             NaN  200 Block EDISON AV        NaN   
4        LARCENY/THEFT             NaN  100 Block OXFORD AV        NaN   

      city state    zip country   latitude  longitude          created_at  \
0  BUFFALO    NY    NaN     NaN  42.977840 -78.824289 2017-05-22 06:04:48   
1  BUFFALO    NY    NaN     NaN  42.893997 -78.844936 2016-10-10 04:06:33   
2  BUFFALO    NY    NaN     NaN  42.868172 -78.858852 2015-02-25 07:06:19   
3  BUFFALO    NY    NaN     NaN  42.931101 -78.802412 2015-08-24 06:07:27   
4  BUFFALO    NY  14226     NaN  42.966698 -78.818852 2015-03-28 06:06:44   

               updated_at                                    location  \
0  05/28/2017 06:07:24 AM  POINT (-78.8242894263842 42.9778397412646)   
1  10/16/2016 06:08:37 AM    POINT (-78.844935658937 42.893996842697)   
2  03/02/2015 07:12:21 AM    POINT (-78.858852415049 42.868171640149)   
3  08/30/2015 06:08:50 AM    POINT (-78.802412189146 42.931100982182)   
4  04/03/2015 06:07:10 AM              POINT (-78.8188515 42.9666981)   

   hour_of_day day_of_week parent_incident_type  Council Districts  \
0            7      Sunday              Assault                NaN   
1            3      Sunday                Theft                5.0   
2            9     Tuesday              Assault                5.0   
3            8      Friday  Breaking & Entering                8.0   
4            6    Thursday                Theft                NaN   

   Police Districts  Zip Codes  Tracts  year  month  
0               NaN       20.0     NaN  2017      5  
1               3.0        8.0    26.0  2016     10  
2               4.0       19.0    32.0  2015      2  
3               2.0       11.0    63.0  2015      8  
4               NaN        6.0     NaN  2015      3

Now the created_at column will be set as the be set as the index, this will help to extract year 2018 which is our year of interest

In [4]:
# set the created_at column as the index
df1.set_index('created_at', inplace=True)
df1.head()

incident_id case_number       incident_datetime  \
created_at                                                             
2017-05-22 06:04:48    806461606  17-1410281  05/21/2017 07:53:00 AM   
2016-10-10 04:06:33    775993048  16-2830116  10/09/2016 03:17:25 AM   
2015-02-25 07:06:19    701886568  15-0550952  02/24/2015 09:59:00 AM   
2015-08-24 06:07:27    728282183  15-2350781  06/19/2015 08:00:00 AM   
2015-03-28 06:06:44    711185846  15-0860249  03/26/2015 06:00:00 AM   

                    incident_type_primary incident_description  \
created_at                                                       
2017-05-22 06:04:48               ASSAULT              ASSAULT   
2016-10-10 04:06:33         LARCENY/THEFT        LARCENY/THEFT   
2015-02-25 07:06:19               ASSAULT              ASSAULT   
2015-08-24 06:07:27              BURGLARY             BURGLARY   
2015-03-28 06:06:44         LARCENY/THEFT        LARCENY/THEFT   

                     clearance_type            address_1  address_2     city  \
created_at                                                                     
2017-05-22 06:04:48             NaN  1 Block FOUNTAIN PA        NaN  BUFFALO   
2016-10-10 04:06:33             NaN    1 Block HERMAN ST        NaN  BUFFALO   
2015-02-25 07:06:19             NaN    100 Block HAMBURG        NaN  BUFFALO   
2015-08-24 06:07:27             NaN  200 Block EDISON AV        NaN  BUFFALO   
2015-03-28 06:06:44             NaN  100 Block OXFORD AV        NaN  BUFFALO   

                    state    zip country   latitude  longitude  \
created_at                                                       
2017-05-22 06:04:48    NY    NaN     NaN  42.977840 -78.824289   
2016-10-10 04:06:33    NY    NaN     NaN  42.893997 -78.844936   
2015-02-25 07:06:19    NY    NaN     NaN  42.868172 -78.858852   
2015-08-24 06:07:27    NY    NaN     NaN  42.931101 -78.802412   
2015-03-28 06:06:44    NY  14226     NaN  42.966698 -78.818852   

                                 updated_at  \
created_at                                    
2017-05-22 06:04:48  05/28/2017 06:07:24 AM   
2016-10-10 04:06:33  10/16/2016 06:08:37 AM   
2015-02-25 07:06:19  03/02/2015 07:12:21 AM   
2015-08-24 06:07:27  08/30/2015 06:08:50 AM   
2015-03-28 06:06:44  04/03/2015 06:07:10 AM   

                                                       location  hour_of_day  \
created_at                                                                     
2017-05-22 06:04:48  POINT (-78.8242894263842 42.9778397412646)            7   
2016-10-10 04:06:33    POINT (-78.844935658937 42.893996842697)            3   
2015-02-25 07:06:19    POINT (-78.858852415049 42.868171640149)            9   
2015-08-24 06:07:27    POINT (-78.802412189146 42.931100982182)            8   
2015-03-28 06:06:44              POINT (-78.8188515 42.9666981)            6   

                    day_of_week parent_incident_type  Council Districts  \
created_at                                                                
2017-05-22 06:04:48      Sunday              Assault                NaN   
2016-10-10 04:06:33      Sunday                Theft                5.0   
2015-02-25 07:06:19     Tuesday              Assault                5.0   
2015-08-24 06:07:27      Friday  Breaking & Entering                8.0   
2015-03-28 06:06:44    Thursday                Theft                NaN   

                     Police Districts  Zip Codes  Tracts  year  month  
created_at                                                             
2017-05-22 06:04:48               NaN       20.0     NaN  2017      5  
2016-10-10 04:06:33               3.0        8.0    26.0  2016     10  
2015-02-25 07:06:19               4.0       19.0    32.0  2015      2  
2015-08-24 06:07:27               2.0       11.0    63.0  2015      8  
2015-03-28 06:06:44               NaN        6.0     NaN  2015      3

The newly created index will be sorted so we can have a well structured index in the right order

In [5]:
# Sort the Data
df1 = df1.sort_values('created_at')
df1.head()

incident_id case_number       incident_datetime  \
created_at                                                             
2009-05-28 12:37:52     10066257  09-1390927  05/19/2009 09:21:42 AM   
2009-05-28 12:37:52     10066259  09-1300158  05/10/2009 03:12:00 AM   
2009-05-28 12:37:52     10066256  09-1220204  05/02/2009 03:57:29 AM   
2009-05-28 12:37:52     10066260  09-1321088  05/12/2009 11:25:00 AM   
2009-05-28 12:37:52     10066258  09-1380053  05/18/2009 02:15:00 AM   

                    incident_type_primary  \
created_at                                  
2009-05-28 12:37:52              Homicide   
2009-05-28 12:37:52              Homicide   
2009-05-28 12:37:52              Homicide   
2009-05-28 12:37:52              Homicide   
2009-05-28 12:37:52              Homicide   

                                                  incident_description  \
created_at                                                               
2009-05-28 12:37:52  Buffalo Police are investigating this report o...   
2009-05-28 12:37:52  Buffalo Police are investigating this report o...   
2009-05-28 12:37:52  Buffalo Police are investigating this report o...   
2009-05-28 12:37:52  Buffalo Police are investigating this report o...   
2009-05-28 12:37:52  Buffalo Police are investigating this report o...   

                     clearance_type               address_1  address_2  \
created_at                                                               
2009-05-28 12:37:52             NaN         100 BLOCK JAMES        NaN   
2009-05-28 12:37:52             NaN      3000 BLOCK MAIN ST        NaN   
2009-05-28 12:37:52             NaN     1500 BLOCK BROADWAY        NaN   
2009-05-28 12:37:52             NaN  300 BLOCK MILLICENT AV        NaN   
2009-05-28 12:37:52             NaN     100 BLOCK BEITER WK        NaN   

                        city state  zip country  latitude  longitude  \
created_at                                                             
2009-05-28 12:37:52  Buffalo    NY  NaN      US  42.87924  -78.84228   
2009-05-28 12:37:52  Buffalo    NY  NaN      US  42.94950  -78.82875   
2009-05-28 12:37:52  Buffalo    NY  NaN      US  42.89641  -78.82030   
2009-05-28 12:37:52  Buffalo    NY  NaN      US  42.93510  -78.80216   
2009-05-28 12:37:52  Buffalo    NY  NaN      US  42.93090  -78.79959   

                                 updated_at                    location  \
created_at                                                                
2009-05-28 12:37:52  07/07/2009 01:24:56 PM  POINT (-78.84228 42.87924)   
2009-05-28 12:37:52  07/07/2009 01:24:55 PM   POINT (-78.82875 42.9495)   
2009-05-28 12:37:52  07/07/2009 01:24:54 PM   POINT (-78.8203 42.89641)   
2009-05-28 12:37:52  07/07/2009 01:24:56 PM   POINT (-78.80216 42.9351)   
2009-05-28 12:37:52  07/07/2009 01:24:56 PM   POINT (-78.79959 42.9309)   

                     hour_of_day day_of_week parent_incident_type  \
created_at                                                          
2009-05-28 12:37:52            9     Tuesday             Homicide   
2009-05-28 12:37:52            3      Sunday             Homicide   
2009-05-28 12:37:52            3    Saturday             Homicide   
2009-05-28 12:37:52           11     Tuesday             Homicide   
2009-05-28 12:37:52            2      Monday             Homicide   

                     Council Districts  Police Districts  Zip Codes  Tracts  \
created_at                                                                    
2009-05-28 12:37:52                5.0               3.0       19.0    42.0   
2009-05-28 12:37:52                8.0               2.0       18.0    56.0   
2009-05-28 12:37:52                5.0               3.0        8.0    66.0   
2009-05-28 12:37:52                8.0               2.0       11.0    24.0   
2009-05-28 12:37:52                8.0               2.0       11.0    63.0   

                     year  month  
created_at                        
2009-05-28 12:37:52  20

<a id='item1'></a>

year 2018 will be extracted from the table to reduce the number of rows

In [6]:
# Slice the Date
From = '2018-01-01'
To   = '2018-12-31'
df2 = df1.loc[From:To,:]
df2.head()

incident_id case_number       incident_datetime  \
created_at                                                             
2018-01-01 00:42:09    830595736  17-3650365  12/31/2017 12:59:03 PM   
2018-01-01 00:42:09    830595737  17-3650468  12/31/2017 04:00:00 AM   
2018-01-01 01:24:50    830596483  17-3650580  12/31/2017 06:16:51 AM   
2018-01-01 05:57:21    830607681  17-3650759  12/31/2017 10:40:38 AM   
2018-01-01 08:00:50    830617576  18-0010080  01/01/2018 01:12:10 AM   

                    incident_type_primary  \
created_at                                  
2018-01-01 00:42:09               ASSAULT   
2018-01-01 00:42:09               ROBBERY   
2018-01-01 01:24:50         LARCENY/THEFT   
2018-01-01 05:57:21               ASSAULT   
2018-01-01 08:00:50               ASSAULT   

                                                  incident_description  \
created_at                                                               
2018-01-01 00:42:09  Buffalo Police are investigating this report o...   
2018-01-01 00:42:09  Buffalo Police are investigating this report o...   
2018-01-01 01:24:50  Buffalo Police are investigating this report o...   
2018-01-01 05:57:21  Buffalo Police are investigating this report o...   
2018-01-01 08:00:50  Buffalo Police are investigating this report o...   

                     clearance_type             address_1  address_2     city  \
created_at                                                                      
2018-01-01 00:42:09             NaN  1900 Block SENECA ST        NaN  BUFFALO   
2018-01-01 00:42:09             NaN  900 Block ELMWOOD AV        NaN  BUFFALO   
2018-01-01 01:24:50             NaN  300 Block NIAGARA ST        NaN  BUFFALO   
2018-01-01 05:57:21             NaN     1 Block WEYAND AV        NaN  BUFFALO   
2018-01-01 08:00:50             NaN   1200 Block BROADWAY        NaN  BUFFALO   

                    state  zip country   latitude  longitude  \
created_at                                                     
2018-01-01 00:42:09    NY  NaN     NaN  42.857382 -78.811625   
2018-01-01 00:42:09    NY  NaN     NaN  42.922181 -78.877126   
2018-01-01 01:24:50    NY  NaN     NaN  42.893677 -78.885648   
2018-01-01 05:57:21    NY  NaN     NaN  42.856181 -78.808711   
2018-01-01 08:00:50    NY  NaN     NaN  42.894580 -78.829563   

                                 updated_at  \
created_at                                    
2018-01-01 00:42:09  01/10/2018 01:16:57 AM   
2018-01-01 00:42:09  01/10/2018 01:16:57 AM   
2018-01-01 01:24:50  01/10/2018 01:16:57 AM   
2018-01-01 05:57:21  01/10/2018 01:16:57 AM   
2018-01-01 08:00:50  01/11/2018 04:24:49 PM   

                                                       location  hour_of_day  \
created_at                                                                     
2018-01-01 00:42:09  POINT (-78.8116246602454 42.8573822712742)           12   
2018-01-01 00:42:09   POINT (-78.877125914901 42.9221806828905)            4   
2018-01-01 01:24:50  POINT (-78.8856483842175 42.8936770646296)            6   
2018-01-01 05:57:21  POINT (-78.8087111810937 42.8561807265981)           10   
2018-01-01 08:00:50  POINT (-78.8295628272309 42.8945797140863)            1   

                    day_of_week parent_incident_type  Council Districts  \
created_at                                                                
2018-01-01 00:42:09      Sunday              Assault                6.0   
2018-01-01 00:42:09      Sunday              Robbery                7.0   
2018-01-01 01:24:50      Sunday                Theft                4.0   
2018-01-01 05:57:21      Sunday              Assault                6.0   
2018-01-01 08:00:50      Monday              Assault                5.0   

                     Police Districts  Zip Codes  Tracts  year  month  
created_at                                                             
2018-01-01 00:42:09               4.0       19.0    22.0  2018      1  
2018-01-01 00:42:09            

<a id='item'></a>

Resetting the index so that some of the columns not needed will be finally deleted

In [7]:
df3 = df2.reset_index()
df3.head()

created_at  incident_id case_number       incident_datetime  \
0 2018-01-01 00:42:09    830595736  17-3650365  12/31/2017 12:59:03 PM   
1 2018-01-01 00:42:09    830595737  17-3650468  12/31/2017 04:00:00 AM   
2 2018-01-01 01:24:50    830596483  17-3650580  12/31/2017 06:16:51 AM   
3 2018-01-01 05:57:21    830607681  17-3650759  12/31/2017 10:40:38 AM   
4 2018-01-01 08:00:50    830617576  18-0010080  01/01/2018 01:12:10 AM   

  incident_type_primary                               incident_description  \
0               ASSAULT  Buffalo Police are investigating this report o...   
1               ROBBERY  Buffalo Police are investigating this report o...   
2         LARCENY/THEFT  Buffalo Police are investigating this report o...   
3               ASSAULT  Buffalo Police are investigating this report o...   
4               ASSAULT  Buffalo Police are investigating this report o...   

   clearance_type             address_1  address_2     city state  zip  \
0             NaN  1900 Block SENECA ST        NaN  BUFFALO    NY  NaN   
1             NaN  900 Block ELMWOOD AV        NaN  BUFFALO    NY  NaN   
2             NaN  300 Block NIAGARA ST        NaN  BUFFALO    NY  NaN   
3             NaN     1 Block WEYAND AV        NaN  BUFFALO    NY  NaN   
4             NaN   1200 Block BROADWAY        NaN  BUFFALO    NY  NaN   

  country   latitude  longitude              updated_at  \
0     NaN  42.857382 -78.811625  01/10/2018 01:16:57 AM   
1     NaN  42.922181 -78.877126  01/10/2018 01:16:57 AM   
2     NaN  42.893677 -78.885648  01/10/2018 01:16:57 AM   
3     NaN  42.856181 -78.808711  01/10/2018 01:16:57 AM   
4     NaN  42.894580 -78.829563  01/11/2018 04:24:49 PM   

                                     location  hour_of_day day_of_week  \
0  POINT (-78.8116246602454 42.8573822712742)           12      Sunday   
1   POINT (-78.877125914901 42.9221806828905)            4      Sunday   
2  POINT (-78.8856483842175 42.8936770646296)            6      Sunday   
3  POINT (-78.8087111810937 42.8561807265981)           10      Sunday   
4  POINT (-78.8295628272309 42.8945797140863)            1      Monday   

  parent_incident_type  Council Districts  Police Districts  Zip Codes  \
0              Assault                6.0               4.0       19.0   
1              Robbery                7.0               5.0       12.0   
2                Theft                4.0               1.0       15.0   
3              Assault                6.0               4.0       19.0   
4              Assault                5.0               3.0        8.0   

   Tracts  year  month  
0    22.0  2018      1  
1    76.0  2018      1  
2    55.0  2018      1  
3    22.0  2018      1  
4    34.0  2018      1

<a id='item1'></a>

finally we drop all the coliumns that will not be needed

In [8]:
df3.drop(['created_at', 'year', 'month'], axis=1, inplace=True)
df3.head()

incident_id case_number       incident_datetime incident_type_primary  \
0    830595736  17-3650365  12/31/2017 12:59:03 PM               ASSAULT   
1    830595737  17-3650468  12/31/2017 04:00:00 AM               ROBBERY   
2    830596483  17-3650580  12/31/2017 06:16:51 AM         LARCENY/THEFT   
3    830607681  17-3650759  12/31/2017 10:40:38 AM               ASSAULT   
4    830617576  18-0010080  01/01/2018 01:12:10 AM               ASSAULT   

                                incident_description  clearance_type  \
0  Buffalo Police are investigating this report o...             NaN   
1  Buffalo Police are investigating this report o...             NaN   
2  Buffalo Police are investigating this report o...             NaN   
3  Buffalo Police are investigating this report o...             NaN   
4  Buffalo Police are investigating this report o...             NaN   

              address_1  address_2     city state  zip country   latitude  \
0  1900 Block SENECA ST        NaN  BUFFALO    NY  NaN     NaN  42.857382   
1  900 Block ELMWOOD AV        NaN  BUFFALO    NY  NaN     NaN  42.922181   
2  300 Block NIAGARA ST        NaN  BUFFALO    NY  NaN     NaN  42.893677   
3     1 Block WEYAND AV        NaN  BUFFALO    NY  NaN     NaN  42.856181   
4   1200 Block BROADWAY        NaN  BUFFALO    NY  NaN     NaN  42.894580   

   longitude              updated_at  \
0 -78.811625  01/10/2018 01:16:57 AM   
1 -78.877126  01/10/2018 01:16:57 AM   
2 -78.885648  01/10/2018 01:16:57 AM   
3 -78.808711  01/10/2018 01:16:57 AM   
4 -78.829563  01/11/2018 04:24:49 PM   

                                     location  hour_of_day day_of_week  \
0  POINT (-78.8116246602454 42.8573822712742)           12      Sunday   
1   POINT (-78.877125914901 42.9221806828905)            4      Sunday   
2  POINT (-78.8856483842175 42.8936770646296)            6      Sunday   
3  POINT (-78.8087111810937 42.8561807265981)           10      Sunday   
4  POINT (-78.8295628272309 42.8945797140863)            1      Monday   

  parent_incident_type  Council Districts  Police Districts  Zip Codes  Tracts  
0              Assault                6.0               4.0       19.0    22.0  
1              Robbery                7.0               5.0       12.0    76.0  
2                Theft                4.0               1.0       15.0    55.0  
3              Assault                6.0               4.0       19.0    22.0  
4              Assault                5.0               3.0        8.0    34.0

Checking to see if the index and columns are default list.

In [9]:
print(type(df3.columns))
print(type(df3.index))

<class 'pandas.core.indexes.base.Index'>
<class 'pandas.core.indexes.range.RangeIndex'>


Since the index and columns are not list, we convert them to list using the tolist() method

In [10]:
df3.columns.tolist()
df3.index.tolist()

print (type(df3.columns.tolist()))
print (type(df3.index.tolist()))

<class 'list'>
<class 'list'>


We check the size of the table to confirm the number of rows have been reduced

<a id='item1'></a>

Finally the columns are renamed

In [11]:
df3.rename(columns={'incident_type_primary':'Crime', 'address_1': 'Crime location'}, inplace=True)
df3.head()

incident_id case_number       incident_datetime          Crime  \
0    830595736  17-3650365  12/31/2017 12:59:03 PM        ASSAULT   
1    830595737  17-3650468  12/31/2017 04:00:00 AM        ROBBERY   
2    830596483  17-3650580  12/31/2017 06:16:51 AM  LARCENY/THEFT   
3    830607681  17-3650759  12/31/2017 10:40:38 AM        ASSAULT   
4    830617576  18-0010080  01/01/2018 01:12:10 AM        ASSAULT   

                                incident_description  clearance_type  \
0  Buffalo Police are investigating this report o...             NaN   
1  Buffalo Police are investigating this report o...             NaN   
2  Buffalo Police are investigating this report o...             NaN   
3  Buffalo Police are investigating this report o...             NaN   
4  Buffalo Police are investigating this report o...             NaN   

         Crime location  address_2     city state  zip country   latitude  \
0  1900 Block SENECA ST        NaN  BUFFALO    NY  NaN     NaN  42.857382   
1  900 Block ELMWOOD AV        NaN  BUFFALO    NY  NaN     NaN  42.922181   
2  300 Block NIAGARA ST        NaN  BUFFALO    NY  NaN     NaN  42.893677   
3     1 Block WEYAND AV        NaN  BUFFALO    NY  NaN     NaN  42.856181   
4   1200 Block BROADWAY        NaN  BUFFALO    NY  NaN     NaN  42.894580   

   longitude              updated_at  \
0 -78.811625  01/10/2018 01:16:57 AM   
1 -78.877126  01/10/2018 01:16:57 AM   
2 -78.885648  01/10/2018 01:16:57 AM   
3 -78.808711  01/10/2018 01:16:57 AM   
4 -78.829563  01/11/2018 04:24:49 PM   

                                     location  hour_of_day day_of_week  \
0  POINT (-78.8116246602454 42.8573822712742)           12      Sunday   
1   POINT (-78.877125914901 42.9221806828905)            4      Sunday   
2  POINT (-78.8856483842175 42.8936770646296)            6      Sunday   
3  POINT (-78.8087111810937 42.8561807265981)           10      Sunday   
4  POINT (-78.8295628272309 42.8945797140863)            1      Monday   

  parent_incident_type  Council Districts  Police Districts  Zip Codes  Tracts  
0              Assault                6.0               4.0       19.0    22.0  
1              Robbery                7.0               5.0       12.0    76.0  
2                Theft                4.0               1.0       15.0    55.0  
3              Assault                6.0               4.0       19.0    22.0  
4              Assault                5.0               3.0        8.0    34.0

And this conclueds the cleaning process

<a id='item1'></a>

# Visualizing the crime data on a map

Now that we have a clean dataset, we are going to use geolocator to obtain the coordinates of Bufallo city.

The folium library will be use to plot the map and located the crime areas according to the addresses with their corresponding coordinates given in the dataset

Let's start by first obtaining the coordinate of the city of Buffalo using geolocator

In [12]:
# using geolocator 
address = 'Buffalo, NY'

geolocator = Nominatim(user_agent="bu_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of buffalo are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of buffalo are 42.8867166, -78.8783922.


In [13]:
# latitude and longitude of city of Buffalo
latitude = 42.8867166
longitude = -78.8783922

#### Genrating the map

In [14]:
# using folium to create map of  buffalo and display it
buffalo_map = folium.Map(location=[latitude, longitude], zoom_start=12)

# display the map of city of buffalo
buffalo_map

<a id='item1'></a>

Superimposing the crime crime data into

In [15]:
# using folium
crimes=folium.map.FeatureGroup()
for lat, lng, in zip(df3.latitude, df3.longitude):
    crimes.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=5,
            color='yellow',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )

# add incidents to map
buffalo_map.add_child(crimes)

The markers appears to be clustered and scattered around the neighborhoods, This clusternes can provide confusing information so one way to fix that is to group all the markers into clusters

In [16]:
#using folium plugin
# placing all the crimes into clusters
buffalo_map = folium.Map(location = [latitude, longitude], zoom_start = 12)

# instantiate a mark cluster object for the incidents in the dataframe
crimes = plugins.MarkerCluster().add_to(buffalo_map)

# loop through the dataframe and add each data point to the mark cluster
for lat, lng, label, in zip(df3.latitude, df3.longitude, df3.Crime):
    folium.Marker(
        location=[lat, lng],
        icon=None,
        popup=label,
    ).add_to(crimes)


buffalo_map

#### Describing the Map

+ When you zoom all the way out, all the makers will be grouped ino one global cluster or the total number of crimes recorded in the dataframe.


+ Whenn zoomed in, the clusters will start breaking up into smaller clusters.


+ When zoomed all the way in, this will result into individual cluster with a blue pop-up which pin-points the exact crime location with address in the background.


+ Clicking on the blue pop-pop ribbon will reveal the crime reported in that particular location.
     

<a id='item1'></a>

# Foursquare

We shall use foursquare API to explore the city of Buffalo for venues around the areas where the crimes were reported. Remember that the interest of the firm is to map out areas according to the rates and nature of crimes committed in the area making it easy for them to know which customer to target and which products or services would better suit their security needs.

The dataset that would be used contains the neighborhoods in city Buffalo complete with its coordinates, was also downloaded from [OPEN DATA BUFFALO](https://data.buffalony.gov/browse?limitTo=maps)

<a id='item'></a>

Reading the second datasets that contains list of neighborhoods in the city of Buffalo into a dataframe

In [18]:
buff = pd.read_csv('Neighborhood_Metrics.csv')
buff.head()

Neighborhood Community  ID Neighborhood Abbreviation  \
0  Kensington-Bailey      East  16                        KB   
1            Central   Central   1                        CN   
2    Elmwood Bidwell      West   6                       EBW   
3          Riverside     North  11                        RS   
4         Fruit Belt      East  25                        FB   

   Labor Force Participation Rate  Employment Rate  Private Employment Rate  \
0                           56.41            89.47                    82.11   
1                           55.17            93.43                    80.41   
2                           66.01            94.02                    80.12   
3                           56.06            95.04                    80.33   
4                           40.25            89.76                    75.15   

   Government Employment Rate  Self-Employment Rate  Median Income  \
0                       16.11                  1.78          37240   
1                       16.76                  2.83          54390   
2                       15.57                  4.31          56150   
3                       16.14                  3.52          21570   
4                       14.04                 10.82          25350   

   Poverty Rate  Total Persons  Male Persons  Percent Male Persons  \
0         30.88          14098          6250                 44.33   
1         19.52           3458          1928                 55.75   
2         18.24          15804          7405                 46.86   
3         45.32          10703          4891                 45.70   
4         28.03           2296          1028                 44.77   

   Female Persons  Percent Female Persons  Age < 24  Percent Age < 24  \
0            7848                   55.67      5682             40.30   
1            1530                   44.25       811             23.45   
2            8399                   53.14      6500             41.13   
3            5812                   54.30      4426             41.35   
4            1268                   55.23       666             29.01   

   Age 25 to 44  Percent Age 25 to 44  Age 45 to 64  Percent Age 45 to 64  \
0          3498                 24.81          3395                 24.08   
1          1328                 38.40           858                 24.81   
2          4699                 29.73          2948                 18.65   
3          2911                 27.20          2528                 23.62   
4           347                 15.11           694                 30.23   

   Age 65 >  Percent Age 65 >  White  Percent White  Black  Percent Black  \
0      1523             10.80    887           6.29  12373          87.76   
1       461             13.33   1656          47.89    986          28.51   
2      1657             10.48  11039          69.85   2548          16.12   
3       838              7.83   5261          49.15   1428          13.34   
4       589             25.65    265          11.54   1903          82.88   

   Latinx  Percent Latinx  Asian  Percent Asian  Other  Percent Other  \
0     206            1.46    253           1.79    379           2.69   
1     707           20.45     58           1.68     51           1.47   
2    1066            6.75    699           4.42    452           2.86   
3    2407           22.49   1112          10.39    495           4.62   
4      93            4.05      0           0.00     35           1.52   

   Total Occupancy Units  Occupied Units  Percent Occupied Units  \
0                   6492            5674                   87.40   
1                   1957            1631                   83.34   
2                   7143            6170                   86.38   
3                   4831            4130                   85.49   
4                   1333             854                   64.07   

   Vacant Units  Percent Vacant Units  Other Vacant Units  \
0           818                 

<a id='item1'></a>

selecting the only the features will needed for the analysis

In [19]:
b_neigh = buff[['Neighborhood', 'Latitude', 'Longitude']]
b_neigh.head()

Neighborhood   Latitude  Longitude
0  Kensington-Bailey  42.939776 -78.809881
1            Central  42.875966 -78.877250
2    Elmwood Bidwell  42.924511 -78.874531
3          Riverside  42.954950 -78.901916
4         Fruit Belt  42.899160 -78.860605

<a id='item1'></a>

Generating a secong map to locate the neighborhoods and superimpose the venues that will be extraacted from foursquare

In [20]:
# latitude and longitude of city of Buffalo
latitude = 42.8867166
longitude = -78.8783922

In [21]:
# create map and display it
buffalo_map2 = folium.Map(location=[latitude, longitude], zoom_start=12)

# display the map of city of buffalo
buffalo_map2

<a id='item1'></a>

#### Superimposing the data in the map

In [22]:
neighborhood=folium.map.FeatureGroup()
for lat, lng, in zip(b_neigh.Latitude, b_neigh.Longitude):
    neighborhood.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=5,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.6
        )
    )

# add neighborhood to map
buffalo_map2.add_child(neighborhood)

Looking at the map, one could easily observe that the neighborhoods are scattered areas where the crime were reported

now that the map look all set with the neighborhood locations. Next step is to get the names of venues around this neighborhoods

defining the foursquare API keys

In [23]:
CLIENT_ID= 'xxxxxxxxxxxxxxxxxxxxxx'
CLIENT_SECRET= 'xxxxxxxxxxxxxxxxx'
ACCESS_TOKEN= 'xxxxxxxxxxxxxxxxxx'
VERSION='20180605'
LIMIT = 100

In [24]:
radius = 500
LIMIT = 100

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id=CLIENT_ID&client_secret=CLIENT_SECRET&oauth_token={}&v=20180605&ll=,-78.8783922&radius=500&limit=100'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

All the venues will be extracted with these lines of code

In [25]:
buffalo_venues = getNearbyVenues(names=b_neigh['Neighborhood'],
                                   latitudes= b_neigh['Latitude'],
                                   longitudes= b_neigh['Longitude']
                                  )


Kensington-Bailey
Central
Elmwood Bidwell
Riverside
Fruit Belt
Pratt-Willert
University Heights
Delavan Grider
Kaisertown
Lower West Side
Elmwood Bryant
Lovejoy
Fillmore-Leroy
Seneca-Cazenovia
Black Rock
Central Park
West Side
Hopkins-Tifft
South Park
Schiller Park
Hamlin Park
Broadway Fillmore
North Park
Parkside
Upper West Side
Genesee-Moselle
Kenfield
First Ward
West Hertel
Ellicott
Masten Park
Grant-Amherst
Seneca Babcock
MLK Park
Allentown


Checking the first five row to see if we have a clean and complete venue infomation and categories

In [26]:
buffalo_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Kensington-Bailey              42.939776              -78.809881   
1  Kensington-Bailey              42.939776              -78.809881   
2  Kensington-Bailey              42.939776              -78.809881   
3  Kensington-Bailey              42.939776              -78.809881   
4  Kensington-Bailey              42.939776              -78.809881   

                             Venue  Venue Latitude  Venue Longitude  \
0                     Statler City       42.887706       -78.877718   
1                   Niagara Square       42.886556       -78.878107   
2                      Osteria 166       42.887629       -78.876464   
3  New Era Flagship Store: Buffalo       42.888891       -78.877346   
4         Public Espresso + Coffee       42.884952       -78.873359   

      Venue Category  
0        Event Space  
1              Plaza  
2  Trattoria/Osteria  
3           Boutique  
4        Coffee Shop

Renaming the columns

In [27]:
buffalo_venues.rename(columns={'Venue Latitude':'V_Lat', 'Venue Longitude':'V_Long'}, inplace=True)

<a id='item1'></a>

## Methodology<a name="Methodology"></a>

Our focus is to direct our search for areas that the firm can quickly set up the business and hit the ground running with the information they have about the crimes in the city and where to specifically pitch there tents

The first step involved data input and wrangling the crime dataset to extract features required for the analysis.

Secondly the crime locations(latitude and longitude) was used to pin the points to the map, revealing in much better details, in picture, where the crimes were committed.

The third steps involves extracting the neighborhoods with their respective coordinates and used Foursquare API to extract the venues in each of the neighborhoods using their respective coordinates.
these venues were then plotted on the map revealing their locations in the city.

<a id='item=1'></a>

## Analysis <a name="Analysis"></a>

plotting the graph and analysing the plots to see which areas would be an ideal spot to really set up shop and which businesses are located in that region. All these would be done with the aid from the visual plot of the graph

Plotting the venue locations into the map

In [28]:
neighborhood_venues=folium.map.FeatureGroup()
for lat, lng, in zip(buffalo_venues.V_Lat, buffalo_venues.V_Long):
    neighborhood.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=5,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.6
        )
    )

# add neighborhood to map
buffalo_map2.add_child(neighborhood_venues)

A quick view on the map shows that majority of this venues are clustered around downtown of the city which also happen to have one of the highest reported cases of crimes of variuos degree.

Getting the list of potential clients in the city

In [30]:
buffalo_venues['Venue Category'].value_counts()

Lawyer                        630
Hotel                         210
Sandwich Place                210
Pizza Place                   175
Coffee Shop                   140
Food                          140
Bus Stop                      105
Plaza                         105
Cocktail Bar                   70
Business Service               70
Boutique                       70
Art Gallery                    70
Bar                            70
Café                           70
Whisky Bar                     35
Convenience Store              35
Intersection                   35
Wine Bar                       35
Clothing Store                 35
Mediterranean Restaurant       35
Theater                        35
Restaurant                     35
Farmers Market                 35
Brewery                        35
Ice Cream Shop                 35
Steakhouse                     35
Hotel Bar                      35
Financial or Legal Service     35
Burger Joint                   35
Trattoria/Oste

In [31]:
df_clients = buffalo_venues['Venue Category'].value_counts()

In [32]:
possible_clients=pd.DataFrame(df_clients)
possible_clients

Venue Category
Lawyer                                 630
Hotel                                  210
Sandwich Place                         210
Pizza Place                            175
Coffee Shop                            140
Food                                   140
Bus Stop                               105
Plaza                                  105
Cocktail Bar                            70
Business Service                        70
Boutique                                70
Art Gallery                             70
Bar                                     70
Café                                    70
Whisky Bar                              35
Convenience Store                       35
Intersection                            35
Wine Bar                                35
Clothing Store                          35
Mediterranean Restaurant                35
Theater                                 35
Restaurant                              35
Farmers Market                          35
Brewery                                 35
Ice Cream Shop                          35
Steakhouse                              35
Hotel Bar                               35
Financial or Legal Service              35
Burger Joint                            35
Trattoria/Osteria                       35
Beer Bar                                35
Breakfast Spot                          35
Nightclub                               35
Other Repair Shop                       35
Gym                                     35
Park                                    35
Mexican Restaurant                      35
Greek Restaurant                        35
Home Service                            35
Pharmacy                                35
Deli / Bodega                           35
Gym / Fitness Center                    35
Sports Bar                              35
Scenic Lookout                          35
Hot Dog Joint                           35
Seafood Restaurant                      35
Office                                  35
Light Rail Station                      35
Event Space                             35
Music Venue                             35
Escape Room                             35
Pub                                     35
French Restaurant                       35

Resetting the index

In [33]:
possible_clients.reset_index()

index  Venue Category
0                       Lawyer             630
1                        Hotel             210
2               Sandwich Place             210
3                  Pizza Place             175
4                  Coffee Shop             140
5                         Food             140
6                     Bus Stop             105
7                        Plaza             105
8                 Cocktail Bar              70
9             Business Service              70
10                    Boutique              70
11                 Art Gallery              70
12                         Bar              70
13                        Café              70
14                  Whisky Bar              35
15           Convenience Store              35
16                Intersection              35
17                    Wine Bar              35
18              Clothing Store              35
19    Mediterranean Restaurant              35
20                     Theater              35
21                  Restaurant              35
22              Farmers Market              35
23                     Brewery              35
24              Ice Cream Shop              35
25                  Steakhouse              35
26                   Hotel Bar              35
27  Financial or Legal Service              35
28                Burger Joint              35
29           Trattoria/Osteria              35
30                    Beer Bar              35
31              Breakfast Spot              35
32                   Nightclub              35
33           Other Repair Shop              35
34                         Gym              35
35                        Park              35
36          Mexican Restaurant              35
37            Greek Restaurant              35
38                Home Service              35
39                    Pharmacy              35
40               Deli / Bodega              35
41        Gym / Fitness Center              35
42                  Sports Bar              35
43              Scenic Lookout              35
44               Hot Dog Joint              35
45          Seafood Restaurant              35
46                      Office              35
47          Light Rail Station              35
48                 Event Space              35
49                 Music Venue              35
50                 Escape Room              35
51                         Pub              35
52           French Restaurant              35

And finally renaming the columns

In [35]:
possible_clients.rename(columns={'index':'Potential Customers', 'Venue Category':'Counts'}, inplace=True)
possible_clients

Counts
Lawyer                         630
Hotel                          210
Sandwich Place                 210
Pizza Place                    175
Coffee Shop                    140
Food                           140
Bus Stop                       105
Plaza                          105
Cocktail Bar                    70
Business Service                70
Boutique                        70
Art Gallery                     70
Bar                             70
Café                            70
Whisky Bar                      35
Convenience Store               35
Intersection                    35
Wine Bar                        35
Clothing Store                  35
Mediterranean Restaurant        35
Theater                         35
Restaurant                      35
Farmers Market                  35
Brewery                         35
Ice Cream Shop                  35
Steakhouse                      35
Hotel Bar                       35
Financial or Legal Service      35
Burger Joint                    35
Trattoria/Osteria               35
Beer Bar                        35
Breakfast Spot                  35
Nightclub                       35
Other Repair Shop               35
Gym                             35
Park                            35
Mexican Restaurant              35
Greek Restaurant                35
Home Service                    35
Pharmacy                        35
Deli / Bodega                   35
Gym / Fitness Center            35
Sports Bar                      35
Scenic Lookout                  35
Hot Dog Joint                   35
Seafood Restaurant              35
Office                          35
Light Rail Station              35
Event Space                     35
Music Venue                     35
Escape Room                     35
Pub                             35
French Restaurant               35

<a id='items1'></a>

## Results and Discussion <a name="Results"></a>

The analysis has shown that Buffalo offers a great opportunity for a security firm with novel products and services that can easily be marketed to potential customers. The List of The business in Buffalo was extracted and tabulated and the total counts of each looks very convincing enough for the team to start making head way into the city.

With more businesses clustered around the city centre, this insight would also help them to set up their office around the city center and gradually move into other areas far from the city center

<a id='item1'></a>

## Conclusion <a name="Conclusion"></a>

The aim of this project was to answer the three questions raised by my friend in order to help himmake approach plans in setting up a security business in a new city. Datasets from the city of Buffalo, which of course would be the perfect place to gather the data, was used in conjunction with folium, geolocator, and geopy to plot the map and locate new areas that was in the original datasets.

Over 3000 potential customers were revealed more with neighborhoods where each are located. The crime rates where also plotted on the locations the were reported abd the spread across the city.

Finally this project can be useful for anyone planning to relocate to city of Buffalo and is concerned about which area would be best safe to live in(Although this would need further analysis), but insights can ve drawn from the map. Our major focus is to help in locating areas where crimes were reported and use the numbers together with their locations to make decisions as a security firm moving into a new country. This project would be useful to local councils and police departments.

